In [542]:
#generate all possible time frames from a list of years
def generate_time_frames(years):
    time_frames = []
    for i in range(len(years)-1):
        for j in range(i+1, len(years)):
            time_frames.append(f"{years[i]}-{years[j]}")
    return time_frames

# #generate only year over year time frames from a list of years
# def generate_time_frames(years):
#     time_frames = []
#     for i in range(len(years)-1):
#         time_frames.append(f"{years[i]}-{years[i+1]}")
#     return time_frames
#change calcs
# def calculate_changes(df, columns, time_frames, years):
#     for column in columns:
#         for time_frame in time_frames:
#             start_year, end_year = years[time_frames.index(time_frame)], years[time_frames.index(time_frame) + 1]
#             df[f'{column} % Change', 'None', f'{time_frame}'] = percentchange(df[(column, end_year, 'None')], df[(column, start_year, 'None')])
#             df[f'{column} Change', 'None', f'{time_frame}'] = (df[(column, end_year, 'None')] - df[(column, start_year, 'None')])

#     return df

def calculate_changes(df, columns, time_frames, years):
    for column in columns:
        for time_frame in time_frames:
            start_year, end_year = time_frame.split('-')
            df[f'{column} % Change', 'None', f'{time_frame}'] = percentchange(df[(column, int(end_year), 'None')], df[(column, int(start_year), 'None')])
            df[f'{column} Change', 'None', f'{time_frame}'] = (df[(column, int(end_year), 'None')] - df[(column, int(start_year), 'None')])

    return df

#functions
def percentchange(x, y):
    try:
        return ((x - y)*100/y)
    except ZeroDivisionError:
        return 0
def realchange(x, y):
    return x-y

In [543]:
import pandas as pd
import numpy as np
import requests
from collections import deque
from functools import reduce
import matplotlib.pyplot as plt
#pd.options.display.float_format = '{:,.0f}'.format
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.width', 150)
pd.options.mode.chained_assignment = None  # default='warn'
from warnings import simplefilter
simplefilter(action="ignore", category=pd.errors.PerformanceWarning)
import sys
sys.path.append("../../Functions and Dictionaries") # Adds higher directory to python modules path
import geodict
import geodict
namestocommon = geodict.namestocommon
geotogeoid = geodict.geotogeoid
GNRC = geodict.GNRC
KY = geodict.KY
censusplaces = geodict.censusplaces
import sqlite3 as sq

# This notebook outlines the download and formatting process for the HUD residential building permits dataset for counties and places in the GNRC operating region.

There are two figures needed from this information, one is a history of all permits and one is a current snapshot of the diversity of residential permits. The downloading interface is kind of spotty, so you have to download in two separate batches. First, historical data for all single and multifamily (we can add these for total permits and it's interesting to see both). Next, current year for single, multi, and then all of the unit number options.

Go to this page: https://socds.huduser.gov/permits/  
##### Download 1: Historical data for all single and multifamily  
+ Under "Main Criteria" select "States and Counties"  
+ Under "Periodicity" select "Annual"  
+ Under "Select State(s)" select "Tennessee", then select "Show Counties and Jurisdictions for Selected States"  
+ Under "Select Counties", highlight all counties in the GNRC region, check the box for "county total", and show/select all under "Select Permitting Jurisdictions" 
+ Under "Select Year(s), select all available years  
+ Under "Select Series", select multifamily and single family  
+ Finally, select the "Get Data" button  
This will populate a page with the information in table format. Scroll to the bottom and download in excel or csv format. 

Save as a csv in the "Data Downloads" folder and import as downloaded.

##### Download 2
+ Select the geographies the same way as above  
+ Select the most recent year  
+ "Get Data"  
+ Download and save

In [544]:
new_data = pd.read_csv('../Data Downloads/HUD_20222023addon.csv')

In [545]:
new_data.head()

Location  Year                                Series  Series Code  Permits
0  Cheatham County  2022                           Total Units            1      301
1  Cheatham County  2023                           Total Units            1      285
2  Cheatham County  2022     Units in Single-Family Structures            2      301
3  Cheatham County  2023     Units in Single-Family Structures            2      208
4  Cheatham County  2022  Units in All Multi-Family Structures            3        0

In [546]:
new_data['Series'].unique()

array(['Total Units', 'Units in Single-Family Structures',
       'Units in All Multi-Family Structures',
       'Units in 2-unit Multi-Family Structures',
       'Units in 3- and 4-unit Multi-Family Structures',
       'Units in 5+ Unit Multi-Family Structures'], dtype=object)

In [547]:
new_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 948 entries, 0 to 947
Data columns (total 5 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   Location     948 non-null    object
 1   Year         948 non-null    int64 
 2   Series       948 non-null    object
 3   Series Code  948 non-null    int64 
 4   Permits      948 non-null    int64 
dtypes: int64(3), object(2)
memory usage: 37.2+ KB


In [548]:
new_data['Series'] = new_data['Series'].replace({'Units in All Multi-Family Structures': 'Units in Multi-Family Structures'})
thelist = ['Units in Multi-Family Structures', 'Units in Single-Family Structures']
years = ['2022', '2023']
new_data['Year'] = new_data['Year'].astype(str)
new_data = new_data.loc[(new_data['Year'].isin(years)) & (new_data['Series'].isin(thelist))]


In [549]:
new_data.head()

Location  Year                             Series  Series Code  Permits
2   Cheatham County  2022  Units in Single-Family Structures            2      301
3   Cheatham County  2023  Units in Single-Family Structures            2      208
4   Cheatham County  2022   Units in Multi-Family Structures            3        0
5   Cheatham County  2023   Units in Multi-Family Structures            3       77
14  Davidson County  2022  Units in Single-Family Structures            2     4036

In [550]:
new_data['Series'].unique()

array(['Units in Single-Family Structures',
       'Units in Multi-Family Structures'], dtype=object)

In [551]:
#import high level permit data for all years and disaggregated permits for most recent year
data = pd.read_csv('../Data Downloads/HUD_AllBuildingPermits_AllYears.csv')

In [552]:
#examine
data.tail(10)

Location  Year                            Series Series Code Permits
5871  WILSON COUNTY UNINCORPORATED AREA  2012  Units in Multi-Family Structures           3       0
5872  WILSON COUNTY UNINCORPORATED AREA  2013  Units in Multi-Family Structures           3       0
5873  WILSON COUNTY UNINCORPORATED AREA  2014  Units in Multi-Family Structures           3       0
5874  WILSON COUNTY UNINCORPORATED AREA  2015  Units in Multi-Family Structures           3       0
5875  WILSON COUNTY UNINCORPORATED AREA  2016  Units in Multi-Family Structures           3       2
5876  WILSON COUNTY UNINCORPORATED AREA  2017  Units in Multi-Family Structures           3       2
5877  WILSON COUNTY UNINCORPORATED AREA  2018  Units in Multi-Family Structures           3       2
5878  WILSON COUNTY UNINCORPORATED AREA  2019  Units in Multi-Family Structures           3       0
5879  WILSON COUNTY UNINCORPORATED AREA  2020  Units in Multi-Family Structures           3       0
5880  WILSON COUNTY UNINCORPORATED AREA  2021  Units in Multi-Family Structures           3       0

In [553]:
dfs = [data, new_data]
data = pd.concat(dfs)

In [554]:
data = data.loc[data['Year'] != 'Year']

In [555]:
data['Year'].unique()

array(['1980', '1981', '1982', '1983', '1984', '1985', '1986', '1987',
       '1988', '1989', '1990', '1991', '1992', '1993', '1994', '1995',
       '1996', '1997', '1998', '1999', '2000', '2001', '2002', '2003',
       '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011',
       '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019',
       '2020', '2021', '2022', '2023'], dtype=object)

In [556]:
#If you examine the data download in excel, you can see that the headers repeat every few rows, delete these by indexing 
data = data.loc[data['Location'] != 'Location']

In [557]:
#strip extra spaces
data['Location'] = data['Location'].str.strip()

We have three different target geographies that are downloaded: counties, unincorporated areas, and places. We can split these up to concatenate later as the data cleaning processes will be different. For now, we are only taking geographies within the GNRC 14 county operating region. You can see from the download that all counties contain the string "County", and that unincorporated areas contain the string "COUNTY".

In [558]:
counties = data[data['Location'].str.contains('County')]

In [559]:
#append the state for use later
counties['Location'] = counties['Location'] + ", Tennessee"

Counties are ready to go, now for Unincorporated Areas

In [560]:
#unincorporated areas were in all capital letters
unincorporated = data[data['Location'].str.contains('COUNTY')]

In [561]:
region = ['CHEATHAM COUNTY UNINCORPORATED AREA', 'DAVIDSON COUNTY UNINCORPORATED AREA', 'DICKSON COUNTY UNINCORPORATED AREA', 
          'HOUSTON COUNTY UNINCORPORATED AREA', 'HUMPHREYS COUNTY UNINCORPORATED AREA', 'MAURY COUNTY UNINCORPORATED AREA', 
          'MONTGOMERY COUNTY UNINCORPORATED AREA', 'ROBERTSON COUNTY UNINCORPORATED AREA', 'RUTHERFORD COUNTY UNINCORPORATED AREA', 
          'STEWART COUNTY UNINCORPORATED AREA', 'SUMNER COUNTY UNINCORPORATED AREA', 'TROUSDALE COUNTY UNINCORPORATED AREA', 
          'WILLIAMSON COUNTY UNINCORPORATED AREA', 'WILSON COUNTY UNINCORPORATED AREA']

#Davidson, Houston, Humphreys nor Stewart have unincorporated lines

In [562]:
unincdict = {'CHEATHAM COUNTY UNINCORPORATED AREA': 'Cheatham Unincorporated', 'DICKSON COUNTY UNINCORPORATED AREA': "Dickson Unincorporated", 
             'MAURY COUNTY UNINCORPORATED AREA': 'Maury Unincorporated', 'MONTGOMERY COUNTY UNINCORPORATED AREA': 'Montgomery Unincorporated', 
             'ROBERTSON COUNTY UNINCORPORATED AREA': 'Robertson Unincorporated', 'RUTHERFORD COUNTY UNINCORPORATED AREA': 'Rutherford Unincorporated',
             'SUMNER COUNTY UNINCORPORATED AREA': 'Sumner Unincorporated', 'TROUSDALE COUNTY UNINCORPORATED AREA': 'Trousdale Unincorporated', 
             'WILLIAMSON COUNTY UNINCORPORATED AREA': 'Williamson Unincorporated', 'WILSON COUNTY UNINCORPORATED AREA': 'Wilson Unincorporated'}
unincorporated['Location'] = unincorporated['Location'].replace(unincdict)

In [563]:
unincorporated['Location'].unique()

array(['Cheatham Unincorporated', 'Dickson Unincorporated',
       'Maury Unincorporated', 'Montgomery Unincorporated',
       'Robertson Unincorporated', 'Rutherford Unincorporated',
       'Sumner Unincorporated', 'Trousdale Unincorporated',
       'Williamson Unincorporated', 'Wilson Unincorporated'], dtype=object)

In [564]:
test = unincorporated.loc[unincorporated['Location'] == 'Wilson Unincorporated']
test

Location  Year                             Series Series Code Permits
5797  Wilson Unincorporated  1980  Units in Single-Family Structures           2     222
5798  Wilson Unincorporated  1981  Units in Single-Family Structures           2     158
5799  Wilson Unincorporated  1982  Units in Single-Family Structures           2     211
5800  Wilson Unincorporated  1983  Units in Single-Family Structures           2     466
5801  Wilson Unincorporated  1984  Units in Single-Family Structures           2     480
5802  Wilson Unincorporated  1985  Units in Single-Family Structures           2     514
5803  Wilson Unincorporated  1986  Units in Single-Family Structures           2     912
5804  Wilson Unincorporated  1987  Units in Single-Family Structures           2     882
5805  Wilson Unincorporated  1988  Units in Single-Family Structures           2     540
5806  Wilson Unincorporated  1989  Units in Single-Family Structures           2     437
5807  Wilson Unincorporated  1990  Units in Single-Family Structures           2     408
5808  Wilson Unincorporated  1991  Units in Single-Family Structures           2     301
5809  Wilson Unincorporated  1992  Units in Single-Family Structures           2     402
5810  Wilson Unincorporated  1993  Units in Single-Family Structures           2     509
5811  Wilson Unincorporated  1994  Units in Single-Family Structures           2     555
5812  Wilson Unincorporated  1995  Units in Single-Family Structures           2     551
5813  Wilson Unincorporated  1996  Units in Single-Family Structures           2     552
5814  Wilson Unincorporated  1997  Units in Single-Family Structures           2     574
5815  Wilson Unincorporated  1998  Units in Single-Family Structures           2     618
5816  Wilson Unincorporated  1999  Units in Single-Family Structures           2     671
5817  Wilson Unincorporated  2000  Units in Single-Family Structures           2     383
5818  Wilson Unincorporated  2001  Units in Single-Family Structures           2     405
5819  Wilson Unincorporated  2002  Units in Single-Family Structures           2     340
5820  Wilson Unincorporated  2003  Units in Single-Family Structures           2     433
5821  Wilson Unincorporated  2004  Units in Single-Family Structures           2     492
5822  Wilson Unincorporated  2005  Units in Single-Family Structures           2     624
5823  Wilson Unincorporated  2006  Units in Single-Family Structures           2     583
5824  Wilson Unincorporated  2007  Units in Single-Family Structures           2     476
5825  Wilson Unincorporated  2008  Units in Single-Family Structures           2     226
5826  Wilson Unincorporated  2009  Units in Single-Family Structures           2     166
5827  Wilson Unincorporated  2010  Units in Single-Family Structures           2     146
5828  Wilson Unincorporated  2011  Units in Single-Family Structures           2     166
5829  Wilson Unincorporated  2012  Units in Single-Family Structures           2     202
5830  Wilson Unincorporated  2013  Units in Single-Family Structures           2     319
5831  Wilson Unincorporated  2014  Units in Single-Family Structures           2     284
5832  Wilson Unincorporated  2015  Units in Single-Family Structures           2     324
5833  Wilson Unincorporated  2016  Units in Single-Family Structures           2     450
5834  Wilson Unincorporated  2017  Units in Single-Family Structures           2     392
5835  Wilson Unincorporated  2018  Units in Single-Family Structures           2     402
5836  Wilson Unincorporated  2019  Units in Single-Family Structures           2     378
5837  Wilson Unincorporated  2020  Units in Single-Family Structures           2     423
5838  Wilson Unincorporated  2021  Units in Single-Family Structures           2     504
5839  Wilson Unincorporated  1980   Units in Multi-Family Structures           3      20
5840  Wilson Unincorporated  1981   Units in Multi-Family Structures           3       0
5841  Wilson U

Places are going to be more difficult, we're looking for the following: 
Adams city, Tennessee: Robertson  
Ashland City town, Tennessee: Cheatham  
Belle Meade city, Tennessee: Davidson  
Berry Hill city, Tennessee: Davidson  
Brentwood city, Tennessee: Williamson  
Burns town, Tennessee: Dickson  
Cedar Hill city, Tennessee: Robertson  
Charlotte town, Tennessee: Dickson  
Clarksville city, Tennessee: Montgomery  
Columbia city, Tennessee: Maury  
Coopertown town, Tennessee: Robertson  
Cross Plains city, Tennessee: Robertson  
Cumberland City town, Tennessee: Stewart  
Dickson city, Tennessee: Dickson  
Dover city, Tennessee: Stewart  
Eagleville city, Tennessee: Rutherford  
Erin city, Tennessee: Houston  
Fairview city, Tennessee: Williamson  
Forest Hills city, Tennessee: Davidson  
Franklin city, Tennessee: Williamson  
Gallatin city, Tennessee: Sumner  
Goodlettsville city, Tennessee: Davidson/Sumner  
Greenbrier town, Tennessee: Robertson  
Hendersonville city, Tennessee: Sumner  
Kingston Springs town, Tennessee: Cheatham  
La Vergne city, Tennessee: Rutherford  
Lafayette city, Tennessee: Macon  
Lebanon city, Tennessee: Wilson  
McEwen city, Tennessee: Humphreys  
Millersville city, Tennessee: Robertson/Sumner  
Mitchellville city, Tennessee: Sumner  
Mount Juliet city, Tennessee: Wilson  
Mount Pleasant city, Tennessee: Maury  
Murfreesboro city, Tennessee: Rutherford  
Nashville-Davidson metropolitan government (balance): Davidson  
New Johnsonville city, Tennessee: Humphreys  
Nolensville town, Tennessee: Williamson  
Oak Hill city, Tennessee: Davidson  
Pegram town, Tennessee: Cheatham  
Pleasant View city, Tennessee: Cheatham  
Portland city, Tennessee: Robertson/Sumner  
Ridgetop city, Tennessee: Davidson/Robertson  
Slayden town, Tennessee: Dickson  
Smyrna town, Tennessee: Rutherford  
Spring Hill city, Tennessee: Maury/Williamson  
Springfield city, Tennessee: Robertson  
Tennessee Ridge town, Tennessee: Houston/Stewart  
Thompson's Station town, Tennessee: Williamson  
Vanleer town, Tennessee: Dickson  
Watertown city, Tennessee: Wilson  
Waverly city, Tennessee: Humphreys  
Westmoreland town, Tennessee: Sumner  
White Bluff town, Tennessee: Dickson  
White House city, Tennessee: Robertson/Sumner    

The downloaded data is in all caps, and doesn't have the ", Tennessee" of the "town.. city... etc.". There are 54 records. We can reverse index into the geographies that are *not* counties or unincorporated areas, reformat the capital letters, and then I'll make a list of only the first word of the place to run through and see how close we can get that way.


In [565]:
#for places filter out the counties and unincorporated areas
place = data[~data['Location'].str.contains('County')]
place = place[~place['Location'].str.contains('COUNTY')]

In [566]:
#this makes the first letter of each word uppercase and the reset lowercase
place['Location'] = place['Location'].str.title()

In [567]:
#I've gone through the excel document to see what these are named - hopefully it is consistent year to year so that this saves time.
places = ["Adams", "Ashland City Town", "Belle Meade", "Berry Hill", "Brentwood", "Burns Town",  "Charlotte Town", "Clarksville", "Columbia", "Coopertown Town", 
          "Cross Plains", "Cumberland City Town", "Dickson", "Dover", "Eagleville", "Erin", "Fairview", "Forest Hills", "Franklin", "Gallatin", "Goodlettsville", 
          "Greenbrier Town","Hendersonville", "Kingston Springs Town", "La Vergne", "Lafayette", "Lebanon", "Mcewen", "Millersville", "Mitchellville Town", 
          "Mount Juliet", "Mount Pleasant", "Murfreesboro", "Nashville-Davidson", "New Johnsonville", "Nolensville Town", "Oak Hill", "Pegram Town", "Pleasant View", 
          "Portland", "Ridgetop Town","Smyrna Town", "Spring Hill Town", "Springfield", "Tennessee Ridge Town", "Thompsons Station Town", "Watertown", 
          "Waverly", "Westmoreland Town", "White Bluff Town", "White House"]

In [568]:
#filter both df's with the list of places above
place = place.loc[place['Location'].isin(places)].reset_index(drop = True)

In [569]:
#transpose in order to rename
transp = place.set_index('Location').transpose()

In [570]:
transp.head()

Location                                 Adams                              Adams                              Adams  \
Year                                      1980                               1981                               1982   
Series       Units in Single-Family Structures  Units in Single-Family Structures  Units in Single-Family Structures   
Series Code                                  2                                  2                                  2   
Permits                                      0                                  0                                  0   

Location                                 Adams                              Adams                              Adams  \
Year                                      1983                               1984                               1985   
Series       Units in Single-Family Structures  Units in Single-Family Structures  Units in Single-Family Structures   
Series Code                                  2                                  2                                  2   
Permits                                      0                                  0                                  0   

Location                                 Adams                              Adams                              Adams  \
Year                                      1986                               1987                               1988   
Series       Units in Single-Family Structures  Units in Single-Family Structures  Units in Single-Family Structures   
Series Code                                  2                                  2                                  2   
Permits                                      0                                  0                                  0   

Location                                 Adams                              Adams                              Adams  \
Year                                      1989                               1990                               1991   
Series       Units in Single-Family Structures  Units in Single-Family Structures  Units in Single-Family Structures   
Series Code                                  2                                  2                                  2   
Permits                                      0                                  3                                  3   

Location                                 Adams                              Adams                              Adams  \
Year                                      1992                               1993                               1994   
Series       Units in Single-Family Structures  Units in Single-Family Structures  Units in Single-Family Structures   
Series Code                                  2                                  2                                  2   
Permits                                      3                                  1                                  3   

Location                                 Adams                              Adams                              Adams  \
Year                                      1995                               1996                               1997   
Series       Units in Single-Family Structures  Units in Single-Family Structures  Units in Single-Family Structures   
Series Code                                  2                                  2                                  2   
Permits                                      1                                  0                                  0   

Location                                 Adams                              Adams                              Adams  \
Year                                      1998                               1999                               2000   
Series       Units in Single-Family Structures  Units in Single-Family Structures  Units in Single-Family Structures   
Series Code                       

In [571]:
#don't even try to use the custom module for this - this part is taking their weird names and making them into Census correct names
transp = transp.rename(columns = {"Adams": 'Adams city, Tennessee', "Ashland City Town":'Ashland City town, Tennessee',
                                  "Belle Meade": 'Belle Meade city, Tennessee', "Berry Hill": 'Berry Hill city, Tennessee', 
                                  "Brentwood": 'Brentwood city, Tennessee', "Burns Town": 'Burns town, Tennessee',  
                                  "Charlotte Town": 'Charlotte town, Tennessee',  "Clarksville": 'Clarksville city, Tennessee', 
                                  "Columbia": 'Columbia city, Tennessee', "Coopertown Town": 'Coopertown town, Tennessee', 
                                  "Cross Plains": 'Cross Plains city, Tennessee', "Cumberland City Town":'Cumberland City town, Tennessee', 
                                  "Dickson": 'Dickson city, Tennessee', "Dover": 'Dover city, Tennessee', 
                                  "Eagleville": 'Eagleville city, Tennessee', "Erin": 'Erin city, Tennessee', 
                                  "Fairview": 'Fairview city, Tennessee', "Forest Hills": 'Forest Hills city, Tennessee', 
                                  "Franklin": 'Franklin city, Tennessee', "Gallatin": 'Gallatin city, Tennessee', 
                                  "Goodlettsville": 'Goodlettsville city, Tennessee', "Greenbrier Town": 'Greenbrier town, Tennessee',
                                  "Hendersonville": 'Hendersonville city, Tennessee', "Kingston Springs Town": 'Kingston Springs town, Tennessee', 
                                  "La Vergne": 'La Vergne city, Tennessee', "Lafayette": 'La Vergne city, Tennessee', 
                                  "Lebanon": 'Lebanon city, Tennessee', "Mcewen": 'McEwen city, Tennessee', 
                                  "Millersville": 'Millersville city, Tennessee', "Mitchellville Town": 'Mitchellville city, Tennessee', 
                                  "Mount Juliet": 'Mount Juliet city, Tennessee', "Mount Pleasant": 'Mount Pleasant city, Tennessee', 
                                  "Murfreesboro": 'Murfreesboro city, Tennessee', "Nashville-Davidson": "Nashville-Davidson metropolitan government (balance)", 
                                  "New Johnsonville": 'New Johnsonville city, Tennessee', "Nolensville Town": 'Nolensville town, Tennessee', 
                                  "Oak Hill": 'Oak Hill city, Tennessee', "Pegram Town": 'Pegram town, Tennessee', 
                                  "Pleasant View": 'Pleasant View city, Tennessee', "Portland": 'Portland city, Tennessee', 
                                  "Ridgetop Town": 'Ridgetop city, Tennessee',"Smyrna Town": 'Smyrna town, Tennessee', 
                                  "Spring Hill Town": 'Spring Hill city, Tennessee', "Springfield": 'Springfield city, Tennessee', 
                                  "Tennessee Ridge Town": 'Tennessee Ridge town, Tennessee', "Thompsons Station Town": "Thompson's Station town, Tennessee",
                                  "Watertown": 'Watertown city, Tennessee', "Waverly": 'Waverly city, Tennessee', 
                                  "Westmoreland Town": 'Westmoreland town, Tennessee', "White Bluff Town": 'White Bluff town, Tennessee', 
                                  "White House": 'White House city, Tennessee'})

In [572]:
#transpose back and reset index without dropping
place = transp.transpose().reset_index()

In [573]:
#concatenate the annual time series data and the current data
dfs = [counties, unincorporated, place]
df = pd.concat(dfs)

In [574]:
#rename location to name and drop series code
df = df.rename(columns = {'Location':'NAME'})

In [575]:
#pivot these dataframes
df = df.pivot(index = ['NAME', 'Year'], columns = 'Series', values = 'Permits')

In [576]:
df = df.reset_index(drop = False)

In [577]:
df.head()

Series                   NAME  Year Units in Multi-Family Structures Units in Single-Family Structures
0       Adams city, Tennessee  1980                                0                                 0
1       Adams city, Tennessee  1981                                0                                 0
2       Adams city, Tennessee  1982                                0                                 0
3       Adams city, Tennessee  1983                                0                                 0
4       Adams city, Tennessee  1984                                0                                 0

In [578]:
df['NAME'].value_counts()

NAME
Adams city, Tennessee                                   44
Oak Hill city, Tennessee                                44
Robertson Unincorporated                                44
Robertson County, Tennessee                             44
Ridgetop city, Tennessee                                44
Portland city, Tennessee                                44
Pleasant View city, Tennessee                           44
Pegram town, Tennessee                                  44
Nolensville town, Tennessee                             44
Rutherford Unincorporated                               44
Nashville-Davidson metropolitan government (balance)    44
Murfreesboro city, Tennessee                            44
Mount Pleasant city, Tennessee                          44
Mount Juliet city, Tennessee                            44
Montgomery Unincorporated                               44
Montgomery County, Tennessee                            44
Rutherford County, Tennessee                       

In [579]:
#there's a few newbies in 2022 data... let's drop them for now I can deal later
thelist = ['Dover city, Tennessee', 'Waverly city, Tennessee', 'New Johnsonville city, Tennessee', 'Erin city, Tennessee', 'Tennessee Ridge town, Tennessee', 
           'Cumberland City town, Tennessee', 'McEwen city, Tennessee']
df = df.loc[~df['NAME'].isin(thelist)]

In [580]:
df['Year'].value_counts()

Year
1980    67
1981    67
2004    67
2005    67
2006    67
2007    67
2008    67
2009    67
2010    67
2011    67
2012    67
2013    67
2014    67
2015    67
2016    67
2017    67
2018    67
2019    67
2020    67
2021    67
2022    67
2003    67
2002    67
2001    67
1990    67
1982    67
1983    67
1984    67
1985    67
1986    67
1987    67
1988    67
1989    67
1991    67
2000    67
1992    67
1993    67
1994    67
1995    67
1996    67
1997    67
1998    67
1999    67
2023    67
Name: count, dtype: int64

In [581]:
years = list(df['Year'].unique().astype(str))

In [582]:
data = df.set_index(['NAME', 'Year']).transpose()
cols = data.columns
data[cols] = data[cols].astype(float)
for year in years:
    GNRCCounties = [data[('Stewart County, Tennessee', '{}'.format(year))],data[('Montgomery County, Tennessee', '{}'.format(year))],
                    data[('Houston County, Tennessee', '{}'.format(year))],data[('Humphreys County, Tennessee', '{}'.format(year))],
                    data[('Dickson County, Tennessee', '{}'.format(year))],data[('Cheatham County, Tennessee', '{}'.format(year))],
                    data[('Robertson County, Tennessee', '{}'.format(year))],data[('Sumner County, Tennessee', '{}'.format(year))],
                    data[('Davidson County, Tennessee', '{}'.format(year))],data[('Wilson County, Tennessee', '{}'.format(year))],
                    data[('Trousdale County, Tennessee', '{}'.format(year))],data[('Williamson County, Tennessee', '{}'.format(year))],
                    data[('Rutherford County, Tennessee', '{}'.format(year))]]
    data[('GNRC', '{}'.format(year))] = sum(GNRCCounties)
    GNRCCountiesAll = [data[('Stewart County, Tennessee', '{}'.format(year))],data[('Montgomery County, Tennessee', '{}'.format(year))],
                       data[('Houston County, Tennessee', '{}'.format(year))],data[('Humphreys County, Tennessee', '{}'.format(year))],
                       data[('Dickson County, Tennessee', '{}'.format(year))],data[('Cheatham County, Tennessee', '{}'.format(year))],
                       data[('Robertson County, Tennessee', '{}'.format(year))],data[('Sumner County, Tennessee', '{}'.format(year))],
                       data[('Davidson County, Tennessee', '{}'.format(year))],data[('Wilson County, Tennessee', '{}'.format(year))],
                       data[('Trousdale County, Tennessee', '{}'.format(year))],data[('Williamson County, Tennessee', '{}'.format(year))],
                       data[('Rutherford County, Tennessee', '{}'.format(year))],data[('Maury County, Tennessee', '{}'.format(year))]]
    data[('GNRC Region', '{}'.format(year))] = sum(GNRCCountiesAll)
    MPOCounties = [data[('Robertson County, Tennessee', '{}'.format(year))],data[('Sumner County, Tennessee', '{}'.format(year))],
                   data[('Davidson County, Tennessee', '{}'.format(year))],data[('Wilson County, Tennessee', '{}'.format(year))],
                   data[('Williamson County, Tennessee', '{}'.format(year))],data[('Rutherford County, Tennessee', '{}'.format(year))],
                   data[('Maury County, Tennessee', '{}'.format(year))]]
    data[('MPO', '{}'.format(year))] = sum(MPOCounties)
data = data.transpose().reset_index()
df = data

In [583]:
#reset the indices and cast the names of the columns, set the columns needed for mathematical operations to float datatypes
#df = df.reset_index(drop = False)
cols = ['Units in Multi-Family Structures', 'Units in Single-Family Structures']
df[cols] = df[cols].astype(float)
#df['Year'] = df['Year'].astype(float)

In [584]:
#aggregate all units for the annual dataframe and rename disaggregated units for the current dataframe
df['Units in All Structures'] = df['Units in Multi-Family Structures'] + df['Units in Single-Family Structures']

In [585]:
df['Year'] = df['Year'].astype(str).astype(int)

In [586]:
#create a list of years from the dataframe to pass through our "generate time frames" function to create a list of all possible time frames - need this here for later
years = list(df['Year'].unique())
time_frames = generate_time_frames(years)

In [587]:
df_nochange = df

In [588]:
df_nochange.head()

Series                   NAME  Year  Units in Multi-Family Structures  Units in Single-Family Structures  Units in All Structures
0       Adams city, Tennessee  1980                               0.0                                0.0                      0.0
1       Adams city, Tennessee  1981                               0.0                                0.0                      0.0
2       Adams city, Tennessee  1982                               0.0                                0.0                      0.0
3       Adams city, Tennessee  1983                               0.0                                0.0                      0.0
4       Adams city, Tennessee  1984                               0.0                                0.0                      0.0

In [589]:
#pivot the table and create a multiindex of year and column header
cols = list(df.columns)
cols.remove('NAME')
cols.remove('Year')
df_pivot = df.pivot_table(index='NAME', columns=['Year'], values= cols)
df_pivot.head(3)

Series                       Units in All Structures                                                                                            \
Year                                            1980 1981 1982  1983  1984 1985  1986  1987 1988 1989  1990  1991  1992 1993  1994  1995  1996   
NAME                                                                                                                                             
Adams city, Tennessee                            0.0  0.0  0.0   0.0   0.0  0.0   0.0   0.0  0.0  0.0   3.0   3.0   3.0  1.0   3.0   1.0   0.0   
Ashland City town, Tennessee                     0.0  0.0  0.0   0.0   0.0  0.0   0.0   0.0  0.0  0.0  84.0  51.0  23.0  6.0  18.0  30.0  25.0   
Belle Meade city, Tennessee                      0.0  0.0  7.0  32.0  20.0  9.0  12.0  10.0  6.0  9.0   9.0   2.0   3.0  8.0   7.0  12.0   3.0   

Series                                                                                                                                               \
Year                          1997  1998   1999  2000  2001   2002   2003  2004  2005  2006  2007  2008   2009 2010 2011 2012 2013 2014  2015  2016   
NAME                                                                                                                                                  
Adams city, Tennessee          0.0   0.0    0.0   0.0   0.0    0.0    0.0   0.0   0.0   0.0   0.0   0.0    0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   
Ashland City town, Tennessee  21.0  88.0  136.0  75.0  97.0  101.0  115.0  72.0  16.0  26.0  36.0  14.0  222.0  3.0  0.0  0.0  2.0  4.0   7.0  25.0   
Belle Meade city, Tennessee   13.0   5.0   10.0   4.0   9.0   16.0   11.0  10.0   8.0   7.0   8.0   6.0    5.0  2.0  0.0  0.0  8.0  4.0  13.0   7.0   

Series                                                                  Units in Multi-Family Structures                                            \
Year                          2017  2018  2019  2020   2021  2022  2023                             1980 1981 1982  1983  1984 1985 1986 1987 1988   
NAME                                                                                                                                                 
Adams city, Tennessee          0.0   0.0   0.0   0.0    0.0   0.0   0.0                              0.0  0.0  0.0   0.0   0.0  0.0  0.0  0.0  0.0   
Ashland City town, Tennessee  63.0  50.0  24.0  23.0  193.0  57.0  73.0                              0.0  0.0  0.0   0.0   0.0  0.0  0.0  0.0  0.0   
Belle Meade city, Tennessee    9.0  11.0   7.0   6.0   14.0   9.0   4.0                              0.0  0.0  0.0  22.0  10.0  0.0  0.0  0.0  0.0   

Series                                                                                                                                             \
Year                         1989 1990 1991  1992 1993 1994 1995 1996 1997  1998   1999  2000  2001  2002  2003  2004  2005 2006 2007 2008   2009   
NAME                                                                                                                                                
Adams city, Tennessee         0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0   0.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.0  0.0  0.0    0.0   
Ashland City town, Tennessee  0.0  8.0  3.0  12.0  0.0  0.0  8.0  7.0  7.0  73.0  134.0  40.0  68.0  70.0  96.0  48.0  10.0  0.0  0.0  0.0  216.0   
Belle Meade city, Tennessee   0.0  0.0  0.0   0.0  0.0  0.0  4.0  0.0  0.0   0.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.0  0.0  0.0    0.0   

Series                                                                                                Units in Single-Family Structures            \
Year                         2010 2011 2012 2013 2014 2015 2016 2017 2018 2019 2020   2021 2022  2023                              1980 1981 1982   
NAME                                                                                                                      

In [590]:
#add a level to the multiindex to accomodate the time period metrics
df_pivot.columns = pd.MultiIndex.from_tuples([(col[0], col[1], 'None') for col in df_pivot.columns])
df_pivot.head(3)

Units in All Structures                                                                                            \
                                                1980 1981 1982  1983  1984 1985  1986  1987 1988 1989  1990  1991  1992 1993  1994  1995  1996   
                                                None None None  None  None None  None  None None None  None  None  None None  None  None  None   
NAME                                                                                                                                             
Adams city, Tennessee                            0.0  0.0  0.0   0.0   0.0  0.0   0.0   0.0  0.0  0.0   3.0   3.0   3.0  1.0   3.0   1.0   0.0   
Ashland City town, Tennessee                     0.0  0.0  0.0   0.0   0.0  0.0   0.0   0.0  0.0  0.0  84.0  51.0  23.0  6.0  18.0  30.0  25.0   
Belle Meade city, Tennessee                      0.0  0.0  7.0  32.0  20.0  9.0  12.0  10.0  6.0  9.0   9.0   2.0   3.0  8.0   7.0  12.0   3.0   

                                                                                                                                                     \
                              1997  1998   1999  2000  2001   2002   2003  2004  2005  2006  2007  2008   2009 2010 2011 2012 2013 2014  2015  2016   
                              None  None   None  None  None   None   None  None  None  None  None  None   None None None None None None  None  None   
NAME                                                                                                                                                  
Adams city, Tennessee          0.0   0.0    0.0   0.0   0.0    0.0    0.0   0.0   0.0   0.0   0.0   0.0    0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   
Ashland City town, Tennessee  21.0  88.0  136.0  75.0  97.0  101.0  115.0  72.0  16.0  26.0  36.0  14.0  222.0  3.0  0.0  0.0  2.0  4.0   7.0  25.0   
Belle Meade city, Tennessee   13.0   5.0   10.0   4.0   9.0   16.0   11.0  10.0   8.0   7.0   8.0   6.0    5.0  2.0  0.0  0.0  8.0  4.0  13.0   7.0   

                                                                        Units in Multi-Family Structures                                            \
                              2017  2018  2019  2020   2021  2022  2023                             1980 1981 1982  1983  1984 1985 1986 1987 1988   
                              None  None  None  None   None  None  None                             None None None  None  None None None None None   
NAME                                                                                                                                                 
Adams city, Tennessee          0.0   0.0   0.0   0.0    0.0   0.0   0.0                              0.0  0.0  0.0   0.0   0.0  0.0  0.0  0.0  0.0   
Ashland City town, Tennessee  63.0  50.0  24.0  23.0  193.0  57.0  73.0                              0.0  0.0  0.0   0.0   0.0  0.0  0.0  0.0  0.0   
Belle Meade city, Tennessee    9.0  11.0   7.0   6.0   14.0   9.0   4.0                              0.0  0.0  0.0  22.0  10.0  0.0  0.0  0.0  0.0   

                                                                                                                                                   \
                             1989 1990 1991  1992 1993 1994 1995 1996 1997  1998   1999  2000  2001  2002  2003  2004  2005 2006 2007 2008   2009   
                             None None None  None None None None None None  None   None  None  None  None  None  None  None None None None   None   
NAME                                                                                                                                                
Adams city, Tennessee         0.0  0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0   0.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.0  0.0  0.0    0.0   
Ashland City town, Tennessee  0.0  8.0  3.0  12.0  0.0  0.0  8.0  7.0  7.0  73.0  134.0  40.0  68.0  70.0  96.0  48.0  10.0  0.0  0.0  0.0  216.0   
Bel

In [591]:
df_pivot.info()

<class 'pandas.core.frame.DataFrame'>
Index: 70 entries, Adams city, Tennessee to Wilson Unincorporated
Columns: 132 entries, ('Units in All Structures', 1980, 'None') to ('Units in Single-Family Structures', 2023, 'None')
dtypes: float64(132)
memory usage: 72.7+ KB


In [592]:
df_pivot.head()

Units in All Structures                                                                                           \
                                                1980  1981  1982   1983   1984   1985   1986   1987   1988   1989   1990   1991   1992   1993   
                                                None  None  None   None   None   None   None   None   None   None   None   None   None   None   
NAME                                                                                                                                            
Adams city, Tennessee                            0.0   0.0   0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    3.0    3.0    3.0    1.0   
Ashland City town, Tennessee                     0.0   0.0   0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   84.0   51.0   23.0    6.0   
Belle Meade city, Tennessee                      0.0   0.0   7.0   32.0   20.0    9.0   12.0   10.0    6.0    9.0    9.0    2.0    3.0    8.0   
Berry Hill city, Tennessee                       0.0   0.0   0.0    0.0    0.0    1.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
Brentwood city, Tennessee                       68.0  54.0  85.0  370.0  218.0  449.0  328.0  250.0  259.0  228.0  160.0  153.0  282.0  351.0   

                                                                                                                                                     \
                               1994   1995   1996   1997   1998   1999   2000   2001   2002   2003   2004   2005   2006   2007   2008   2009   2010   
                               None   None   None   None   None   None   None   None   None   None   None   None   None   None   None   None   None   
NAME                                                                                                                                                  
Adams city, Tennessee           3.0    1.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   
Ashland City town, Tennessee   18.0   30.0   25.0   21.0   88.0  136.0   75.0   97.0  101.0  115.0   72.0   16.0   26.0   36.0   14.0  222.0    3.0   
Belle Meade city, Tennessee     7.0   12.0    3.0   13.0    5.0   10.0    4.0    9.0   16.0   11.0   10.0    8.0    7.0    8.0    6.0    5.0    2.0   
Berry Hill city, Tennessee      0.0    0.0    0.0    0.0    8.0   29.0    5.0    0.0    0.0    0.0    0.0    0.0    0.0   43.0    1.0    0.0    0.0   
Brentwood city, Tennessee     317.0  261.0  276.0  186.0  212.0  198.0  171.0  257.0  458.0  605.0  633.0  458.0  502.0  294.0  104.0   65.0  137.0   

                                                                                                                        \
                               2011   2012   2013   2014   2015   2016   2017   2018   2019   2020   2021  2022   2023   
                               None   None   None   None   None   None   None   None   None   None   None  None   None   
NAME                                                                                                                     
Adams city, Tennessee           0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   0.0    0.0   
Ashland City town, Tennessee    0.0    0.0    2.0    4.0    7.0   25.0   63.0   50.0   24.0   23.0  193.0  57.0   73.0   
Belle Meade city, Tennessee     0.0    0.0    8.0    4.0   13.0    7.0    9.0   11.0    7.0    6.0   14.0   9.0    4.0   
Berry Hill city, Tennessee      0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0    0.0   0.0    5.0   
Brentwood city, Tennessee     232.0  253.0  225.0  251.0  240.0  175.0  185.0  139.0  109.0  141.0  147.0  83.0  104.0   

                             Units in Multi-Family Structures                                                                                     \
                                                         1980 1981 1982  1983  1984 1985 1986 1987 1988 1989 1990 19

In [593]:
#get a list of the varaibles to loop through by indexing into the first level only of the column headers
first_level = df_pivot.columns.get_level_values(0).unique().tolist()
first_level

['Units in All Structures',
 'Units in Multi-Family Structures',
 'Units in Single-Family Structures']

In [594]:
#pass the dataframe, the list of variables, time frames, and years through the "calculate change" function
newthing = calculate_changes(df_pivot, first_level, 
                            time_frames = time_frames, years = years)

In [595]:
newthing.head(2)

Units in All Structures                                                                                              \
                                                1980 1981 1982 1983 1984 1985 1986 1987 1988 1989  1990  1991  1992 1993  1994  1995  1996  1997   
                                                None None None None None None None None None None  None  None  None None  None  None  None  None   
NAME                                                                                                                                               
Adams city, Tennessee                            0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   3.0   3.0   3.0  1.0   3.0   1.0   0.0   0.0   
Ashland City town, Tennessee                     0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  84.0  51.0  23.0  6.0  18.0  30.0  25.0  21.0   

                                                                                                                                                    \
                              1998   1999  2000  2001   2002   2003  2004  2005  2006  2007  2008   2009 2010 2011 2012 2013 2014 2015  2016  2017   
                              None   None  None  None   None   None  None  None  None  None  None   None None None None None None None  None  None   
NAME                                                                                                                                                 
Adams city, Tennessee          0.0    0.0   0.0   0.0    0.0    0.0   0.0   0.0   0.0   0.0   0.0    0.0  0.0  0.0  0.0  0.0  0.0  0.0   0.0   0.0   
Ashland City town, Tennessee  88.0  136.0  75.0  97.0  101.0  115.0  72.0  16.0  26.0  36.0  14.0  222.0  3.0  0.0  0.0  2.0  4.0  7.0  25.0  63.0   

                                                                  Units in Multi-Family Structures                                               \
                              2018  2019  2020   2021  2022  2023                             1980 1981 1982 1983 1984 1985 1986 1987 1988 1989   
                              None  None  None   None  None  None                             None None None None None None None None None None   
NAME                                                                                                                                              
Adams city, Tennessee          0.0   0.0   0.0    0.0   0.0   0.0                              0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   
Ashland City town, Tennessee  50.0  24.0  23.0  193.0  57.0  73.0                              0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.0   

                                                                                                                                                   \
                             1990 1991  1992 1993 1994 1995 1996 1997  1998   1999  2000  2001  2002  2003  2004  2005 2006 2007 2008   2009 2010   
                             None None  None None None None None None  None   None  None  None  None  None  None  None None None None   None None   
NAME                                                                                                                                                
Adams city, Tennessee         0.0  0.0   0.0  0.0  0.0  0.0  0.0  0.0   0.0    0.0   0.0   0.0   0.0   0.0   0.0   0.0  0.0  0.0  0.0    0.0  0.0   
Ashland City town, Tennessee  8.0  3.0  12.0  0.0  0.0  8.0  7.0  7.0  73.0  134.0  40.0  68.0  70.0  96.0  48.0  10.0  0.0  0.0  0.0  216.0  0.0   

                                                                                                 Units in Single-Family Structures                 \
                             2011 2012 2013 2014 2015 2016 2017 2018 2019 2020   2021 2022  2023                              1980 1981 1982 1983   
                             None None None None None None None None None None   None None  None                              None None None None   
NAME          

In [596]:
#stack and reset index to bring the year and time frame back down to columns and take geography out of the index, rename the levels to reflect time
newthing = newthing.stack([1, 1])
newthing = newthing.reset_index(drop = False)
newthing = newthing.rename(columns = {'level_1':'Year', 'level_2':'Time Frame'})
newthing.head(2)

NAME  Year Time Frame  Units in All Structures  Units in All Structures % Change  Units in All Structures Change  \
0  Adams city, Tennessee  1980       None                      0.0                               NaN                             NaN   
1  Adams city, Tennessee  1981       None                      0.0                               NaN                             NaN   

   Units in Multi-Family Structures  Units in Multi-Family Structures % Change  Units in Multi-Family Structures Change  \
0                               0.0                                        NaN                                      NaN   
1                               0.0                                        NaN                                      NaN   

   Units in Single-Family Structures  Units in Single-Family Structures % Change  Units in Single-Family Structures Change  
0                                0.0                                         NaN                                       NaN  
1                                0.0                                         NaN                                       NaN

In [597]:
df = newthing

In [598]:
#map the common name to the geoid dict in custom module
df['GEO_ID'] = df['NAME'].map(geotogeoid)
#set source
df['Source'] = 'HUD SOC Annual Data'

In [599]:
df['NAME'].unique()

array(['Adams city, Tennessee', 'Ashland City town, Tennessee',
       'Belle Meade city, Tennessee', 'Berry Hill city, Tennessee',
       'Brentwood city, Tennessee', 'Burns town, Tennessee',
       'Charlotte town, Tennessee', 'Cheatham County, Tennessee',
       'Cheatham Unincorporated', 'Clarksville city, Tennessee',
       'Columbia city, Tennessee', 'Coopertown town, Tennessee',
       'Cross Plains city, Tennessee', 'Davidson County, Tennessee',
       'Dickson County, Tennessee', 'Dickson Unincorporated',
       'Dickson city, Tennessee', 'Eagleville city, Tennessee',
       'Fairview city, Tennessee', 'Forest Hills city, Tennessee',
       'Franklin city, Tennessee', 'GNRC', 'GNRC Region',
       'Gallatin city, Tennessee', 'Goodlettsville city, Tennessee',
       'Greenbrier town, Tennessee', 'Hendersonville city, Tennessee',
       'Houston County, Tennessee', 'Humphreys County, Tennessee',
       'Kingston Springs town, Tennessee', 'La Vergne city, Tennessee',
       'Leba

In [605]:
test = df.loc[(df['NAME'] == 'Watertown city, Tennessee')]
test

NAME  Year Time Frame  Units in All Structures  Units in All Structures % Change  Units in All Structures Change  \
61380  Watertown city, Tennessee  1980       None                      1.0                               NaN                             NaN   
61381  Watertown city, Tennessee  1981       None                      0.0                               NaN                             NaN   
61382  Watertown city, Tennessee  1982       None                      2.0                               NaN                             NaN   
61383  Watertown city, Tennessee  1983       None                      0.0                               NaN                             NaN   
61384  Watertown city, Tennessee  1984       None                      1.0                               NaN                             NaN   
61385  Watertown city, Tennessee  1985       None                      2.0                               NaN                             NaN   
61386  Watertown city, Tennessee  1986       None                      0.0                               NaN                             NaN   
61387  Watertown city, Tennessee  1987       None                     27.0                               NaN                             NaN   
61388  Watertown city, Tennessee  1988       None                      4.0                               NaN                             NaN   
61389  Watertown city, Tennessee  1989       None                      5.0                               NaN                             NaN   
61390  Watertown city, Tennessee  1990       None                      3.0                               NaN                             NaN   
61391  Watertown city, Tennessee  1991       None                      2.0                               NaN                             NaN   
61392  Watertown city, Tennessee  1992       None                      1.0                               NaN                             NaN   
61393  Watertown city, Tennessee  1993       None                      0.0                               NaN                             NaN   
61394  Watertown city, Tennessee  1994       None                      0.0                               NaN                             NaN   
61395  Watertown city, Tennessee  1995       None                      0.0                               NaN                             NaN   
61396  Watertown city, Tennessee  1996       None                      0.0                               NaN                             NaN   
61397  Watertown city, Tennessee  1997       None                     12.0                               NaN                             NaN   
61398  Watertown city, Tennessee  1998       None                      8.0                               NaN                             NaN   
61399  Watertown city, Tennessee  1999       None                      6.0                               NaN                             NaN   
61400  Watertown city, Tennessee  2000       None                      8.0                               NaN                             NaN   
61401  Watertown city, Tennessee  2001       None                      7.0                               NaN                             NaN   
61402  Watertown city, Tennessee  2002       None                      5.0                               NaN                             NaN   
61403  Watertown city, Tennessee  2003       None                      5.0                               NaN                             NaN   
61404  Watertown city, Tennessee  2004       None                      0.0                               NaN                             NaN   
61405  Watertown city, Tennessee  2005       None                      5.0                               NaN                             NaN   
61406  Watertown city, Tennessee  2006       None                      5.0                               NaN                             NaN

In [601]:
df.head()

NAME  Year Time Frame  Units in All Structures  Units in All Structures % Change  Units in All Structures Change  \
0  Adams city, Tennessee  1980       None                      0.0                               NaN                             NaN   
1  Adams city, Tennessee  1981       None                      0.0                               NaN                             NaN   
2  Adams city, Tennessee  1982       None                      0.0                               NaN                             NaN   
3  Adams city, Tennessee  1983       None                      0.0                               NaN                             NaN   
4  Adams city, Tennessee  1984       None                      0.0                               NaN                             NaN   

   Units in Multi-Family Structures  Units in Multi-Family Structures % Change  Units in Multi-Family Structures Change  \
0                               0.0                                        NaN                                      NaN   
1                               0.0                                        NaN                                      NaN   
2                               0.0                                        NaN                                      NaN   
3                               0.0                                        NaN                                      NaN   
4                               0.0                                        NaN                                      NaN   

   Units in Single-Family Structures  Units in Single-Family Structures % Change  Units in Single-Family Structures Change            GEO_ID  \
0                                0.0                                         NaN                                       NaN  1600000US4700200   
1                                0.0                                         NaN                                       NaN  1600000US4700200   
2                                0.0                                         NaN                                       NaN  1600000US4700200   
3                                0.0                                         NaN                                       NaN  1600000US4700200   
4                                0.0                                         NaN                                       NaN  1600000US4700200   

                Source  
0  HUD SOC Annual Data  
1  HUD SOC Annual Data  
2  HUD SOC Annual Data  
3  HUD SOC Annual Data  
4  HUD SOC Annual Data

In [602]:
#export to the SQLite database
conn = sq.connect('../Outputs/HUD.db')
df.to_sql('SingleMulti_Historic', conn, if_exists = 'replace', index = False)

69300